# Выбор локации для скважины

Задача ставится в рамках работы добывающей компании «ГлавРосГосНефть». Нужно решить, где бурить новую скважину.

Предоставлены пробы нефти в трёх регионах: в каждом 10 000 месторождений, где измерили качество нефти и объём её запасов. Постройте модель машинного обучения, которая поможет определить регион, где добыча принесёт наибольшую прибыль. Проанализируйте возможную прибыль и риски техникой *Bootstrap.*

Шаги для выбора локации:

- В избранном регионе ищут месторождения, для каждого определяют значения признаков;
- Строят модель и оценивают объём запасов;
- Выбирают месторождения с самым высокими оценками значений. Количество месторождений зависит от бюджета компании и стоимости разработки одной скважины;
- Прибыль равна суммарной прибыли отобранных месторождений.

# План работ

1. Загрузка и подготовка данных<br>
2. Обуечение модели для каждой Локации:<br>
    2.1. Работа с моделью Локации 0<br>
    2.1.1. Разбиение выборок на обучающую и валидационную 75-25.<br>
    2.1.2. Обучение модели и выполнение предсказания на валидационной выборки. Вычисление RMSE<br>
    2.1.3. Выведение среднего запаса предсказанного сырья на одну скважину и на регион.<br>
    2.2. Работа с моделью Локации 1<br>
    2.2.1. Разбиение выборок на обучающую и валидационную 75-25.<br>
    2.2.2. Обучение модели и выполнение предсказания на валидационной выборки. Вычисление RMSE<br>
    2.2.3. Выведение среднего запаса предсказанного сырья на одну скважину и на регион.<br>
    2.3. Работа с моделью Локации 2<br>
    2.3.1. Разбиение выборок на обучающую и валидационную 75-25.<br>
    2.3.2. Обучение модели и выполнение предсказания на валидационной выборки. Вычисление RMSE<br>
    2.3.3. Выведение среднего запаса предсказанного сырья на одну скважину и на регион.<br>
3. Подготовка к расчету прибыли<br>
    3.1. Вычисление объема сырья на одной скважине, достаточного для безубыточного производства.<br> 
    3.2. Создание функции для расчета суммарной прибыли по региону при разработке 200 новых скважин.<br>
4. Оценка рисков и возможной прибыли <br>
    4.1. Локация 0<br>
    4.1.1. Выбор 200 скважин с наилучшим предсказанным сырьем и получение суммарного объема сырья в Локации.<br> 
    4.1.2.  Рассчет потенциальной прибыли с локации 0<br>
    4.1.2.1. Разбитие предсказаний на 1000 выборок по 500 скважин.<br> 
    4.1.2.2. Поиск средней предсказанной прибыли с Локации 0, вероятность получения отрицательной прибыли и 95% доверительного интервала. <br>
    4.2. Локация 1<br>
    4.2.1. Выбор 200 скважин с наилучшим предсказанным сырьем и получение суммарного объема сырья в Локации.<br> 
    4.2.2.  Рассчет потенциальной прибыли с локации 0<br>
    4.2.2.1. Разбитие предсказаний на 1000 выборок по 500 скважин.<br> 
    4.2.2.2. Поиск средней предсказанной прибыли с Локации 1, вероятность получения отрицательной прибыли и 95% доверительного интервала. <br>
    4.3. Локация 2<br>
    4.3.1. Выбор 200 скважин с наилучшим предсказанным сырьем и получение суммарного объема сырья в Локации.<br> 
    4.3.2.  Рассчет потенциальной прибыли с локации 0<br>
    4.3.2.1. Разбитие предсказаний на 1000 выборок по 500 скважин.<br> 
    4.3.2.2. Поиск средней предсказанной прибыли с Локации 0, вероятность получения отрицательной прибыли и 95% доверительного интервала. <br>
5. Выводы о наиболее перспективной Локации для разработки.<br> 


## Загрузка и подготовка данных

In [54]:
#Импорт библиотек для дальнейшей работы
import pandas as pd
import numpy as np

pd.options.display.float_format = '{:.2f}'.format 
#в дальнейшей таблице очень много знаков после запятой, ограраничим представление двумя.

pd.set_option('display.max_rows', 500) 


from scipy import stats as st 
import random
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error


In [55]:
#Импортируем данные
try:
    location0 = pd.read_csv('datasets/geo_data_0.csv')
    location1 = pd.read_csv('datasets/geo_data_1.csv')
    location2 = pd.read_csv('datasets/geo_data_1.csv')
except:
    location0 = pd.read_csv('geo_data_0.csv')
    location1 = pd.read_csv('geo_data_1.csv')
    location2 = pd.read_csv('geo_data_2.csv')
    
            

### Посмотрим на исходные данные для Локация 0

In [56]:
#посмотрим на локацию 0 
display(location0.head())
location0.info() #посмотрим на типы данных и число строк
location0.duplicated().sum() #посмотрим на дубликаты. Дубликатов нет. 



id    f0    f1   f2  product
0  txEyH  0.71 -0.50 1.22   105.28
1  2acmU  1.33 -0.34 4.37    73.04
2  409Wp  1.02  0.15 1.42    85.27
3  iJLyR -0.03  0.14 2.98   168.62
4  Xdl7t  1.99  0.16 4.75   154.04

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 5 columns):
 #   Column   Non-Null Count   Dtype  
---  ------   --------------   -----  
 0   id       100000 non-null  object 
 1   f0       100000 non-null  float64
 2   f1       100000 non-null  float64
 3   f2       100000 non-null  float64
 4   product  100000 non-null  float64
dtypes: float64(4), object(1)
memory usage: 3.8+ MB


0

Видимых "проблем" с типами данных нет, полных дубликатов нет. 

In [57]:
#Проверим таблицу на наличие пропусков
location0.isna().sum()

id         0
f0         0
f1         0
f2         0
product    0
dtype: int64

In [58]:
#Проверим Локацию 0 на скрытые дубликаты (например, дублируются идентификаторы скважин)

duplices = location0.query('id.duplicated()')['id'] #имеются дублирующиеся id скважин. 
duplices

7530     HZww2
41724    bxg6G
51970    A5aEY
63593    QcMuo
66136    74z30
69163    AGS9W
75715    Tdehs
90815    fiKDv
92341    TtcGQ
97785    bsk9y
Name: id, dtype: object

In [59]:
display(location0.query('id in @duplices').count())
location0.query('id in @duplices').sort_values(by = 'id') #имеются дублирующиеся id скважин. 20 штук


id         20
f0         20
f1         20
f2         20
product    20
dtype: int64

id    f0    f1    f2  product
66136  74z30  1.08 -0.31  6.99   127.64
64022  74z30  0.74  0.46  5.15   140.77
51970  A5aEY -0.18  0.94 -2.09    33.02
3389   A5aEY -0.04  0.16  0.21    89.25
69163  AGS9W -0.93  0.12 -3.66    19.23
42529  AGS9W  1.45 -0.48  0.68   126.37
931    HZww2  0.76  0.37  1.86    30.68
7530   HZww2  1.06 -0.37 10.43   158.83
63593  QcMuo  0.64 -0.47  0.86    64.58
1949   QcMuo  0.51 -0.32 -2.22    75.50
75715  Tdehs  0.11  0.43  3.22    60.96
21426  Tdehs  0.83  0.30 -0.05    96.04
92341  TtcGQ  0.11  1.02  0.91   101.32
60140  TtcGQ  0.57 -0.10  6.44    85.35
89582  bsk9y  0.40 -0.40 10.12   163.43
97785  bsk9y  0.38  0.01  0.16   160.64
41724  bxg6G -0.82  0.55  3.63    93.01
1364   bxg6G  0.41  0.86 -3.65    73.60
16633  fiKDv  0.16  1.03  5.59    95.82
90815  fiKDv  0.05  0.84  6.39   137.35

С одной стороны,  дублирующиеся id скважин могут означать, что какие-то из данных по ним неверные. Мы можем просто удалить эти данные. Однако "дублируется" всео 0,02%, которые и так не влияют на результат наших предсказаний. 
Выбираем соханить таблциу как есть для упрощения процедуры. 

In [60]:
location0['product'].describe()

count   100000.00
mean        92.50
std         44.29
min          0.00
25%         56.50
50%         91.85
75%        128.56
max        185.36
Name: product, dtype: float64

In [61]:
#мы заметили скважину с нулевой производительностью. Посмотрим, сколько их. 
location0.query('product == 0')
#Такая скважина всего одна - вероятно, законсервированная. Мы ее оставим: она не влияет на наши расчеты.

id    f0   f1   f2  product
57263  zCM5W -0.70 0.38 0.24     0.00

Локация 0 имеет числовые характеристики, полных дубликатов и пропусков не обнаружено, таблица содержит 100 000 строк. Тем не менее, 20 идентификаторов скважин дублируют друг друга (два id одинаковых с разными показателями). Это 0,2% от всей выборки. Оставим эти скважины как есть. В среднем скважины Локации 0 дают 92 тыс. баррелей. но максимальные величины - 180 тыс. баррелей. 

### Изучим данные для Локация 1

In [62]:
#посмотрим на локацию 1
display(location1.head())
location1.info() #посмотрим на типы данных и число строк
location1.duplicated().sum() #посмотрим на дубликаты. Дубликатов нет. 



id     f0     f1    f2  product
0  kBEdx -15.00  -8.28 -0.01     3.18
1  62mP7  14.27  -3.48  1.00    26.95
2  vyE1P   6.26  -5.95  5.00   134.77
3  KcrkZ -13.08 -11.51  5.00   137.95
4  AHL4O  12.70  -8.15  5.00   134.77

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 5 columns):
 #   Column   Non-Null Count   Dtype  
---  ------   --------------   -----  
 0   id       100000 non-null  object 
 1   f0       100000 non-null  float64
 2   f1       100000 non-null  float64
 3   f2       100000 non-null  float64
 4   product  100000 non-null  float64
dtypes: float64(4), object(1)
memory usage: 3.8+ MB


0

Видимых "проблем" с типами данных нет, полных дубликатов нет. 

In [63]:
#Проверим таблицу на наличие пропусков
location1.isna().sum()

id         0
f0         0
f1         0
f2         0
product    0
dtype: int64

In [64]:
#Проверим Локацию 1 на скрытые дубликаты (например, дублируются идентификаторы скважин)

duplices = location1.query('id.duplicated()')['id'] #имеются дублирующиеся id скважин. 
duplices

41906    LHZR0
82178    bfPNe
82873    wt4Uk
84461    5ltQ6
Name: id, dtype: object

In [65]:
display(location1.query('id in @duplices').count())
location1.query('id in @duplices').sort_values(by = 'id') #имеются дублирующиеся id скважин. 8 штук


id         8
f0         8
f1         8
f2         8
product    8
dtype: int64

id    f0     f1    f2  product
5849   5ltQ6 -3.44 -12.30  2.00    57.09
84461  5ltQ6 18.21   2.19  3.99   107.81
1305   LHZR0 11.17  -1.95  3.00    80.86
41906  LHZR0 -8.99  -4.29  2.01    57.09
2721   bfPNe -9.49  -5.46  4.01   110.99
82178  bfPNe -6.20  -4.82  3.00    84.04
47591  wt4Uk -9.09  -8.11 -0.00     3.18
82873  wt4Uk 10.26  -9.38  4.99   134.77

Тут дубликатов еще меньше, чем в Локации 0. Оставим их "как есть".

In [66]:
location1['product'].describe()

count   100000.00
mean        68.83
std         45.94
min          0.00
25%         26.95
50%         57.09
75%        107.81
max        137.95
Name: product, dtype: float64

In [67]:
#мы заметили скважину с нулевой производительностью. Посмотрим, сколько их. 
location1.query('product == 0')


id    f0     f1    f2  product
11     OXyvW 16.32  -0.56 -0.00     0.00
13     igmai  6.70  -0.75 -0.01     0.00
62     Qjy5w 21.42  -5.13 -0.00     0.00
63     G6WCj  6.82   3.10 -0.00     0.00
77     MzQhL  6.75 -11.89 -0.00     0.00
...      ...   ...    ...   ...      ...
99936  YrRU8  5.09  -3.98  0.01     0.00
99948  Jbnur  8.28  -9.18  0.00     0.00
99956  aV1cJ 13.34  -1.29  0.01     0.00
99961  Zjbn2 13.85 -11.53 -0.01     0.00
99973  VsayB 12.70  -4.38 -0.00     0.00

[8235 rows x 5 columns]

В регионе на 8% скважин с нулевым производством. Есть смысл заподозрить Локацию в проблемах (возможно с качеством или количеством сырья, возможно, со сложностями в разработке)

Локация 1 имеет числовые характеристики, полных дубликатов и пропусков не обнаружено, таблица содержит 100 000 строк. В среднем скважины Локации 68 тыс. баррелей, однако 8% скважин - пустые. 

### Изучим данные для Локация 2

In [68]:
#посмотрим на локацию 2
display(location2.head())
location2.info() #посмотрим на типы данных и число строк
location2.duplicated().sum() #посмотрим на дубликаты. Дубликатов нет. 



id    f0    f1    f2  product
0  fwXo0 -1.15  0.96 -0.83    27.76
1  WJtFt  0.26  0.27 -2.53    56.07
2  ovLUW  0.19  0.29 -5.59    62.87
3  q6cA6  2.24 -0.55  0.93   114.57
4  WPMUX -0.52  1.72  5.90   149.60

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 5 columns):
 #   Column   Non-Null Count   Dtype  
---  ------   --------------   -----  
 0   id       100000 non-null  object 
 1   f0       100000 non-null  float64
 2   f1       100000 non-null  float64
 3   f2       100000 non-null  float64
 4   product  100000 non-null  float64
dtypes: float64(4), object(1)
memory usage: 3.8+ MB


0

Видимых "проблем" с типами данных нет, полных дубликатов нет. 

In [69]:
#Проверим таблицу на наличие пропусков
location2.isna().sum()

id         0
f0         0
f1         0
f2         0
product    0
dtype: int64

In [70]:
#Проверим Локацию 2 на скрытые дубликаты (например, дублируются идентификаторы скважин)

duplices = location2.query('id.duplicated()')['id'] #имеются дублирующиеся id скважин. 
duplices

43233    xCHr8
49564    VF7Jo
55967    KUPhW
95090    Vcm5J
Name: id, dtype: object

In [71]:
display(location2.query('id in @duplices').count())
location2.query('id in @duplices').sort_values(by = 'id') #имеются дублирующиеся id скважин. 8 штук


id         8
f0         8
f1         8
f2         8
product    8
dtype: int64

id    f0    f1    f2  product
45404  KUPhW  0.23 -1.70  4.99    11.72
55967  KUPhW  1.21  3.18  5.54   132.83
11449  VF7Jo  2.12 -0.86  5.75   181.72
49564  VF7Jo -0.88  0.56  0.72   136.23
44378  Vcm5J -1.23 -2.44  1.22   137.97
95090  Vcm5J  2.59  1.99  2.48    92.33
28039  xCHr8  1.63  0.37 -2.38     6.12
43233  xCHr8 -0.85  2.10  5.60   184.39

Тут дубликатов еще меньше, чем в Локации 0. Оставим их "как есть".

In [72]:
location2['product'].describe()

count   100000.00
mean        95.00
std         44.75
min          0.00
25%         59.45
50%         94.93
75%        130.60
max        190.03
Name: product, dtype: float64

In [73]:
#мы заметили скважину с нулевой производительностью. Посмотрим, сколько их. 
location2.query('product == 0')


id    f0    f1    f2  product
68149  qeefd -0.87 -1.62 -4.13     0.00

Всего одна скважина с нулевой производительностью. 

Локация 2 имеет числовые характеристики, полных дубликатов и пропусков не обнаружено, таблица содержит 100 000 строк. В среднем скважины Локации 92 тыс. баррелей. 

Предварительно можно сделать вывод, что Локация 1 наименее выгодна для разработки: там меньше среднияя и максимальная производительность скважин, а Локаци 2 наиболее перспективна.

In [74]:
import pandas_profiling
location0.profile_report()


Summarize dataset:   0%|          | 0/19 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [75]:
location1.profile_report()

Summarize dataset:   0%|          | 0/19 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [76]:
location2.profile_report()

Summarize dataset:   0%|          | 0/19 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Обучение и проверка модели

## Модель для Локация 0

In [77]:
#Разделим данные на target/features
target0 = location0['product']
features0 = location0.drop(['product', 'id'], axis=1)

In [78]:
#Разделим выборку location на обучающую и валидационную 75:25
features0_valid, features0_train, target0_valid, target0_train = train_test_split(features0, target0, test_size=0.75, random_state=12345)



In [102]:
#Создаем и обучаем модель линейной регрессии

model0 = LinearRegression()
model0.fit(features0_train, target0_train)
predicted_valid0 = model0.predict(features0_valid)
#ищем среднеквадратическую ошибку модели
rmse0 = mean_squared_error(target0_valid, predicted_valid0)**0.5
display(f'Средний запас представленного сырья в скважине на валидационной выборке в Локации0: {predicted_valid0.mean()} тыс. баррелей. RMSE: {rmse0}')
#теперь, чтобы не потерять предсказания, сообщим им индексы соответствующих строк из target_valid
predicted_valid0 = pd.DataFrame(predicted_valid0).set_index(target0_valid.index)
display(predicted_valid0)

'Средний запас представленного сырья в скважине на валидационной выборке в Локации0: 92.68042230714772 тыс. баррелей. RMSE: 37.68019646464799'

0
79723 130.50
53168 103.93
47576 117.65
91606  69.62
91018 100.92
...      ...
4094   99.61
85412 118.10
2177   98.74
77285  94.51
86498 157.78

[25000 rows x 1 columns]

## Модель для Локация 1

In [80]:
#Разделим данные на target/features

target1 = location1['product']
features1 = location1.drop(['product', 'id'], axis=1)

In [81]:
#Разделим выборку location на обучающую и валидационную 75:25
features1_valid, features1_train, target1_valid, target1_train = train_test_split(features1, target1, test_size=0.75, random_state=12345)


In [103]:
#Создаем и обучаем модель линейной регрессии
model1 = LinearRegression()
model1.fit(features1_train, target1_train)
predicted_valid1 = model1.predict(features1_valid)
#ищем среднеквадратическую ошибку модели
rmse1 = mean_squared_error(target1_valid, predicted_valid1)**0.5
display(f'Средний запас представленного сырья в скважине на валидационной выборке в Локации1: {predicted_valid1.mean()} тыс. баррелей. RMSE: {rmse1}')

predicted_valid1 = pd.DataFrame(predicted_valid1).set_index(target1_valid.index)
display(predicted_valid1)

'Средний запас представленного сырья в скважине на валидационной выборке в Локации1: 68.85982082622293 тыс. баррелей. RMSE: 0.8873287354658539'

0
79723   1.04
53168  26.74
47576   2.43
91606  55.37
91018 137.03
...      ...
4094   82.86
85412 108.63
2177  135.18
77285  82.86
86498  83.25

[25000 rows x 1 columns]

### Модель для Локация 2

In [83]:
#Разделим данные на target/features

target2 = location2['product']
features2 = location2.drop(['product', 'id'], axis=1)

In [84]:
#Разделим выборку location на обучающую и валидационную 75:25
features2_valid, features2_train, target2_valid, target2_train = train_test_split(features2, target2, test_size=0.75, random_state=12345)


In [104]:
#Создаем и обучаем модель линейной регрессии
model2 = LinearRegression()
model2.fit(features2_train, target2_train)
predicted_valid2 = model2.predict(features2_valid)
#ищем среднеквадратическую ошибку модели
rmse2 = mean_squared_error(target2_valid, predicted_valid2)**0.5
display(f'Средний запас представленного сырья в скважине на валидационной выборке в Локации1: {predicted_valid2.mean()} тыс. баррелей. RMSE: {rmse2}')

#Сопоставим индексы для предсказаний и фактической производительности скважин
predicted_valid2 = pd.DataFrame(predicted_valid2).set_index(target2_valid.index)
display(predicted_valid2)

'Средний запас представленного сырья в скважине на валидационной выборке в Локации1: 95.06093851120133 тыс. баррелей. RMSE: 40.11167877627781'

0
79723 103.58
53168  56.77
47576 105.81
91606 117.87
91018 103.63
...      ...
4094  131.48
85412 100.13
2177  108.19
77285 104.00
86498  66.66

[25000 rows x 1 columns]

Локация 2 нам предоставляем самые не выгодные перспективы. Модель Локации 0 лучше обучена (RMSE меньше), однако перспективы Локации 2 наилучшие по добыче сырья. 

## Подготовка к расчёту прибыли

In [40]:
# Оценим стоимость разработки 1 скважины в регионе при условии, что будет разрабатываться 200 скважин:
Location_budget = 10_000_000_000
Total_wells_per_location = 200
Single_well_profit = 450_000
Cost_per_well = Location_budget/Total_wells_per_location
#Определим количество баррелей сырья, которые надо получать от скважины для безубыточности: 
Zero_profit_production = Cost_per_well/Single_well_profit
display(f'Для безубыточного производства скважина дложна давать не менее {Zero_profit_production} тыс. баррелей. ')

'Для безубыточного производства скважина дложна давать не менее 111.11111111111111 тыс. баррелей. '

In [42]:
#Средняя предсказанная производительность скважины в Локации 0
predicted_valid0.mean()

92.68042230714745

In [43]:
#Cредняя предсказанная производительность скважины в Локации 1
predicted_valid1.mean()

68.85982082622296

In [44]:
#Средняя предсказанная поизводительность скважины в Локации 2
predicted_valid2.mean()

95.06093851120148

На первый взгляд, сложно ожидать безубыточного производства. Наибольшие шансы имеет Локация 2.

In [136]:
#Напишем функцию для оценки суммарной прибыли с 200 лучших скважин из выборки

def well_profit(predicted_production, target_production):
    predicted_production.columns = ['predicted_production']
    best_200_wells = predicted_production.sort_values(by = 'predicted_production', ascending = False)[0:200].index
    production_best_200_wells = target_production[best_200_wells].sum()
    profit_best_200_wells = Single_well_profit*production_best_200_wells - Location_budget
    return profit_best_200_wells



## Расчёт прибыли и рисков 

### Прибыли и риски Локации 0

In [143]:
#Разделим предсказания по Локации 0 на 1000 выборок по 500 скважин:
revenue0 = [] #это массив, в который будем складывать предсказанную прибыль с каждой предсказанной скважины
state = np.random.RandomState(12345)

for i in range(1000):
    target0_predicted_subsample = predicted_valid0.sample(n = 500, replace=True, random_state=state)
    revenue0.append(well_profit(target0_predicted_subsample, target0_valid))

revenue0 = pd.Series(revenue0)

revenue0.describe() 
#В наших бутстрепных выборках есть варианты и с отрицательной прибылью, и с положительной.

count         1000.00
mean     437498219.36
std      265433210.98
min     -443606451.42
25%      266753359.38
50%      439171545.59
75%      618416839.96
max     1249276852.04
dtype: float64

In [148]:
Roubles_to_billions = 1/1000_000_000

#Найдем вероятность получить убытки
display(f'Вероятность получить отрицательную прибыль для Локации 0: {revenue0[revenue0 < 0].count()/revenue0.count()}')

#Найдем среднюю прибыль по Локации 0

display(f'Средняя  предсказанная прибыль по Локации 0: {revenue0.mean()*Roubles_to_billions} млрд.руб.')

#Найдем 95% доверительный интервал:
lower0 = revenue0.quantile(0.025)
upper0 = revenue0.quantile(0.975)

print(f'95%-ый доверительный интервал для локации 0: {lower0} : {upper0} руб.')


'Вероятность получить отрицательную прибыль для Локации 0: 0.051'

'Средняя  предсказанная прибыль по Локации 0: 0.43749821935565136 млрд.руб.'

95%-ый доверительный интервал для локации 0: -92309821.44262886 : 948439677.045071 руб.


### Прибыли и риски Локации 1

In [152]:
#Разделим локацию 1 на 1000 выборок по 500 скважин:
revenue1 = []
state = np.random.RandomState(1245)

for i in range(1000):
    target1_predicted_subsample = predicted_valid1.sample(n = 500, replace=True, random_state=state)
    revenue1.append(well_profit(target1_predicted_subsample, target1_valid))

revenue1 = pd.Series(revenue1)
display(revenue1.describe())


count         1000.00
mean     439197596.78
std      200822617.84
min     -357097666.97
25%      303464561.08
50%      440615193.18
75%      568264800.76
max     1039164187.58
dtype: float64

In [153]:


#Найдем вероятность получить убытки
display(f'Вероятность получить отрицательную прибыль для Локации 1: {revenue1[revenue1 < 0].count()/revenue1.count()}')

#Найдем среднюю прибыль

display(f'Средняя прибыль по Локации 1: {revenue1.mean()*Roubles_to_billions} млрд. руб')

#Найдем 90% доверительный интервал:
lower1 = revenue1.quantile(0.025)
upper1 = revenue1.quantile(0.975)

print(f'95%-ый доверительный интервал для локации 1: {lower1} : {upper1}')

'Вероятность получить отрицательную прибыль для Локации 1: 0.013'

'Средняя прибыль по Локации 1: 0.43919759677989667 млрд. руб'

95%-ый доверительный интервал для локации 1: 37311475.034512006 : 857380510.209338


### Прибыли и риски Локации 2

In [155]:
#Разделим локацию 2 на 1000 выборок по 500 скважин:
revenue2 = []
state = np.random.RandomState(12456)

for i in range(1000):
    target2_predicted_subsample = predicted_valid2.sample(n = 500, replace=True, random_state=state)
    revenue2.append(well_profit(target2_predicted_subsample, target2_valid))

revenue2 = pd.Series(revenue2)
display(revenue2.describe())


count         1000.00
mean     333862617.98
std      259166935.27
min     -650908540.29
25%      159288315.24
50%      333962102.09
75%      510342885.14
max     1152463657.54
dtype: float64

In [158]:
#Найдем вероятность получить убытки
display(f'Вероятность получить отрицательную прибыль для Локации 2: {revenue2[revenue2 < 0].count()/revenue2.count()}')

#Найдем среднюю прибыль

display(f'Средняя прибыль по Локации 2: {revenue2.mean()*Roubles_to_billions} млрд. руб')

#Найдем 95% доверительный интервал:
lower2 = revenue2.quantile(0.025)
upper2 = revenue2.quantile(0.975)

print(f'95%-ый доверительный интервал для локации 1: {lower2} : {upper2}')


'Вероятность получить отрицательную прибыль для Локации 2: 0.099'

'Средняя прибыль по Локации 2: 0.3338626179771581 млрд. руб'

95%-ый доверительный интервал для локации 1: -157537464.09767282 : 828824047.1203908


С точки зрения рисков и прибыли наилучшая Локация 1. Риск убыточной рзаработки 1,3%, что меньше критическиз 2,5%, укаанных для принятия решения. В среднем мы можем ожидать на 0,43 млрд рублей прибыли с этой Локации. 

# Общий вывод

1. Загрузка и подготовка данных<br>
Исходные данные представлены по 100 000 изученным скважинам. Предварительно можно сделать вывод, что Локация 1 наименее выгодна для разработки: там 8% скважин имеют нулевую производительность, а Локаци 2 наиболее перспективна.
2. Обуечение модели для каждой Локации:<br>
2.1. Работа с моделью Локации 0<br>
'Средний запас представленного сырья в скважине на валидационной выборке в Локации0: 92.6 тыс. баррелей. RMSE: 37.68 
2.2. Работа с моделью Локации 1<br>
Средний запас представленного сырья в скважине на валидационной выборке в Локации1: 68.85  тыс. баррелей. RMSE: 0.88
2.3. Работа с моделью Локации 2<br>
Средний запас представленного сырья в скважине на валидационной выборке в Локации1: 95.06 тыс. баррелей. RMSE: 40.11<br>
Наиболее перспективны Локация 0 и Локация 2.
3. Объем сырья на одной скважине, достаточного для безубыточного производства составит 111.11 тыс. баррелей. Это больше, чем средний объем сырья на скважинах любой из локаций. <br>
4. Оценка рисков и возможной прибыли<br>
4.1 Локация 0<br>
Вероятность получить отрицательную прибыль для Локации 0: 5.1% <br>
Средняя  предсказанная прибыль по Локации 0: 0.437 млрд.руб.<br>
95%-ый доверительный интервал для Локации 0: (-0.092 млрд. руб., 0.948 млрд. руб.) <br>
4.2. Локация 1<br>
Вероятность получить отрицательную прибыль для Локации 1: 1,3%<br>
Средняя прибыль по Локации 1: 0.439 млрд. руб.<br>
95%-ый доверительный интервал для Локации 1: (0.037 млрд. руб., 0.857 млрд. руб.)<br>
4.3. Локация 2<br>
Вероятность получить отрицательную прибыль для Локации 2: 9.9%<br>
'Средняя прибыль по Локации 2: 0.333  млрд. руб.<br>
95%-ый доверительный интервал для локации 2: (-0.157 млрд. руб., 0.828 млрд. руб.)<br>

С точки зрения рисков и прибыли наилучшая Локация 1. Она сулит минимальные риски убытков 1,3% и наибольшую среднюю прибыль. <br>
**Рекомендации**: рекомендуется выбрать для разработок Локацию 1, как наименее рискованную и более перспективную. 
